In [1]:
import matplotlib.pyplot as plt
import numpy as np
%matplotlib osx

import random

In [2]:
def roll(p):
    return random.random() < p


2023-11-28 01:35:38.352 Python[26000:1107446] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:648
XXX lineno: 708, opcode: 124
ERROR:tornado.application:Exception in callback functools.partial(<function Kernel.enter_eventloop.<locals>.advance_eventloop at 0x1095ac720>)
Traceback (most recent call last):
  File "/opt/homebrew/lib/python3.11/site-packages/tornado/ioloop.py", line 738, in _run_callback
    ret = callback()
          ^^^^^^^^^^
  File "/opt/homebrew/lib/python3.11/site-packages/ipykernel/kernelbase.py", line 461, in advance_eventloop
    eventloop(self)
  File "/opt/homebrew/lib/python3.11/site-packages/ipykernel/eventloops.py", line 353, in loop_cocoa
    if kernel.shell_stream.flush(limit=1):
       ^^^^^^^^^^^^^^^^^^^
  File "/opt/homebrew/lib/python3.11/site-packages/traitlets/traitlets.py", line 708, in __get__
    def __get__(self, obj: HasTraits | None, cls: type[t.Any]) -> 

In [3]:
initial_bankroll = 10000
winning_probability = 18/37
initial_bet = 10

money_timesteps = []

casino = [0]
casino_list = []
gambler_values = []
gambler_total = []

def martingale(bankroll, winning_probability, initial_bet):
    gambler_values.append(bankroll)
    if initial_bet>bankroll:
        return
    current_bet = initial_bet
    while bankroll>current_bet:
        bankroll -= current_bet
        casino[0] += current_bet
        if roll(winning_probability):
            bankroll += current_bet*2
            gambler_values.append(bankroll)
            casino[0] -= current_bet*2
            casino_list.append(casino[0])
            gambler_total.append(-1*casino[0])
            return
        else:
            gambler_values.append(bankroll)
            casino_list.append(casino[0])
            gambler_total.append(-1*casino[0])

            current_bet*=2
    return
for i in range(5000):
    martingale(initial_bankroll, winning_probability, initial_bet)
print(casino_list[-1])


21680


In [4]:
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from matplotlib.animation import FFMpegWriter

def update(frame):
    index = frame
    x_data.append(index)
    y_data_casino_vals.append(casino_list[index])
    y_data_gambler_total.append(gambler_total[index])
    y_data_gambler_vals.append(gambler_values[index])
    line_casino_vals.set_data(x_data, y_data_casino_vals)
    line_gambler_total.set_data(x_data, y_data_gambler_total)
    line_gambler_vals.set_data(x_data, y_data_gambler_vals)

    ax.relim()
    ax.autoscale_view()
    return line_casino_vals, line_gambler_total, line_gambler_vals

fig, ax = plt.subplots()
x_data, y_data_casino_vals, y_data_gambler_total, y_data_gambler_vals = [], [], [], []
line_casino_vals, = ax.plot([], [], label='Casino Values')
line_gambler_total, = ax.plot([], [], label='Sum Gambler Gains/Losses')
line_gambler_vals, = ax.plot([], [], label='Gambler Values')

ax.legend()
ani = FuncAnimation(fig, update, frames=range(0, 5000), blit=True)
writer = FFMpegWriter(fps=100, metadata=dict(artist='Me'), bitrate=1800)
ani.save('new.mp4', writer=writer)
plt.show()


In [17]:
temp_val = [0]

def martingale_monte_carlo(bankroll, winning_probability, initial_bet):
    if initial_bet>bankroll:
        return
    current_bet = initial_bet
    while bankroll>current_bet:
        bankroll -= current_bet
        temp_val[0] += current_bet
        if roll(winning_probability):
            bankroll += current_bet*2
            temp_val[0] -= current_bet*2
            return
        else:
            current_bet*=2
    return

vals = []
for i in range(10000):
    for j in range(15000):
        martingale_monte_carlo(10240, 18/38, 10)
    vals.append(temp_val[0])
    temp_val = [0]


In [29]:
plt.clf()
plt.hist(vals, bins = 50)
plt.xlabel("Casino Total Daily Profit")
plt.ylabel("Num. Occurrences")
plt.savefig("bucket_chart")
plt.show()
print(len(vals))

10000
